# Use this to design AI agent as a POC
<h2>初始化</h2>

In [ ]:
# 读取环境变量
from dotenv import load_dotenv
load_dotenv()  # 加载 .env 文件

<hr>
<h2>定义使用搜索引擎</h2>

In [ ]:
from langchain_community.tools.tavily_search import TavilySearchResults

tool = TavilySearchResults(max_results=3)
tools = [tool]
# tool.invoke("What's a 'node' in LangGraph?")

<hr>
<h2>使用通义千问作为LLM</h2>

In [ ]:
# 使用通义千问
from langchain_community.llms import Tongyi

import os

# 初始化通义模型（以qwen-max为例）
llm_tongyi = Tongyi(
    model_name="qwen-turbo",
    dashscope_api_key=os.getenv("DASHSCOPE_API_KEY")
)

<h2>手动实现通义的工具调用流程</h2>

In [ ]:
from typing import List, Dict, Any
from langchain_core.messages import HumanMessage

def manual_tool_invocation(llm: Tongyi, tools: List, query: str) -> str:

    # 0. 调用搜索引擎
    tool.invoke(query)

    # 1. 构建工具描述
    tool_descs = "\n".join([
        f"{tool.name}: {tool.description}\n参数: {tool.args}"
        for tool in tools
    ])
    
    # 2. 构造特殊 prompt
    prompt = f"""请根据问题决定是否需要使用工具。可用工具：
    {tool_descs}
    
    问题：{query}
    
    如果需要使用工具，请严格按以下格式回复：
    ```json
    {{"tool": "工具名", "args": {{"参数名": "参数值"}}}}
    ```
    如果不需要工具，请直接回答问题。"""
    
    # 3. 调用模型
    response = llm.invoke(prompt)
    
    # 4. 解析工具调用
    if "```json" in response:
        try:
            import json
            tool_call = json.loads(response.split("```json")[1].split("```")[0].strip())
            selected_tool = next(t for t in tools if t.name == tool_call["tool"])
            return selected_tool.invoke(tool_call["args"])
        except:
            return f"工具调用失败：{response}"
    
    return response

# 使用示例
# result = manual_tool_invocation(llm_tongyi, tools, "What's a 'node' in LangGraph?")

<h2>定义智能体工作流</h2>

In [ ]:
from typing import Annotated

from typing_extensions import TypedDict

from langgraph.graph import StateGraph, START, END
from langgraph.graph.message import add_messages

class State(TypedDict):
    # Messages have the type "list". The `add_messages` function
    # in the annotation defines how this state key should be updated
    # (in this case, it appends messages to the list, rather than overwriting them)
    messages: Annotated[list, add_messages]

graph_builder = StateGraph(State)

<h2>添加智能体节点</h2>

In [ ]:
def chatbot(state: State):
    # return {"messages": [llm_tongyi.invoke(state["messages"])]}
    return {"messages": [manual_tool_invocation(llm_tongyi, tools, "What's a 'node' in LangGraph?")]}

# The first argument is the unique node name
# The second argument is the function or object that will be called whenever
# the node is used.
graph_builder.add_node("chatbot", chatbot)

<h2>添加工作流起点和终点</h2>

In [ ]:
# 定义起点
graph_builder.add_edge(START, "chatbot")
# 定义终点
graph_builder.add_edge("chatbot", END)

# 完成编辑
graph = graph_builder.compile()

<h2>展示工作流</h2>

In [ ]:
from IPython.display import Image, display

try:
    display(Image(graph.get_graph().draw_mermaid_png()))
except Exception:
    # This requires some extra dependencies and is optional
    pass

<h2>执行工作流</h2>

In [ ]:
# 流式交互函数（适配通义模型）
def stream_graph_updates(user_input: str):
    state = {"messages": [{"role": "user", "content": user_input}]}

    for event in graph.stream(state):
        for value in event.values():
            last_message = value["messages"][-1]
            print(f"Assistant: {last_message}")

while True:
    try:
        user_input = input("User: ")
        print("User: ", user_input)
        if user_input.lower() in ["quit", "exit", "q"]:
            print("Goodbye!")
            break
        stream_graph_updates(user_input)
    except:
        # fallback if input() is not available
        user_input = "What do you know about LangGraph?"
        print("User: " + user_input)
        stream_graph_updates(user_input)
        break